# **Pulsar Classification For Class Prediction**

Datapath

Bootcamp Machine Learning Engineer.

Alan Grosso.

Junio 2023.


# **[1] Librerias**

In [121]:
import re
import os
import itertools
import time
from datetime import date
from datetime import datetime
from pprint import pprint

import pandas as pd
import numpy as np

import seaborn as sns
import matplotlib.pyplot as plt

from ydata_profiling import ProfileReport

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import GridSearchCV
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import auc, roc_curve, roc_auc_score, brier_score_loss
from sklearn.metrics import accuracy_score, precision_score, recall_score, precision_recall_curve, f1_score
from sklearn.metrics import confusion_matrix
from sklearn.metrics import ConfusionMatrixDisplay, PrecisionRecallDisplay
from sklearn.metrics import classification_report

import joblib
from joblib import dump
from joblib import load

import psutil

import warnings
warnings.filterwarnings('ignore')

In [122]:
# Modularizado

%load_ext autoreload
%autoreload 2

from utils.cuantiles import cuantiles
from utils.corr import correlation

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [123]:
# Configuración 

# Formato de números y separador de miles
pd.set_option('display.float_format', '{:,.4f}'.format)

# Width
pd.options.display.width = 0

# Don't wrap repr(DataFrame) across additional lines
pd.set_option('display.expand_frame_repr', False)

# Set max rows displayed in output
pd.set_option('display.max_rows', 10)

# Set max columns displayed in output
pd.set_option('display.max_columns', 500)

# **[2] Importar datos**

In [124]:
df = pd.read_csv('data/Pulsar.csv')
df.shape

(17898, 9)

In [125]:
df.head()

Mean_Integrated      SD      EK  Skewness  Mean_DMSNR_Curve  SD_DMSNR_Curve  EK_DMSNR_Curve  Skewness_DMSNR_Curve  Class
0         140.5625 55.6838 -0.2346   -0.6996            3.1998         19.1104          7.9755               74.2422      0
1         102.5078 58.8824  0.4653   -0.5151            1.6773         14.8601         10.5765              127.3936      0
2         103.0156 39.3416  0.3233    1.0512            3.1212         21.7447          7.7358               63.1719      0
3         136.7500 57.1784 -0.0684   -0.6362            3.6430         20.9593          6.8965               53.5937      0
4          88.7266 40.6722  0.6009    1.1235            1.1789         11.4687         14.2696              252.5673      0

In [126]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17898 entries, 0 to 17897
Data columns (total 9 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   Mean_Integrated       17898 non-null  float64
 1   SD                    17898 non-null  float64
 2   EK                    17898 non-null  float64
 3   Skewness              17898 non-null  float64
 4   Mean_DMSNR_Curve      17898 non-null  float64
 5   SD_DMSNR_Curve        17898 non-null  float64
 6   EK_DMSNR_Curve        17898 non-null  float64
 7   Skewness_DMSNR_Curve  17898 non-null  float64
 8   Class                 17898 non-null  int64  
dtypes: float64(8), int64(1)
memory usage: 1.2 MB


# **[3] EDA**

Análisis de datos

In [127]:
profile = ProfileReport(df, title="Profiling Report", explorative=True)

In [128]:
profile.to_file("data_profiling_report.html")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [129]:
profile.to_notebook_iframe()

Target

In [130]:
df.Class.value_counts()

0    16259
1     1639
Name: Class, dtype: int64

# **[4] Feature Engineering**

Constantes

In [131]:
temp = df.nunique().sort_values(ascending=False)
temp = pd.DataFrame(temp).reset_index()

#temp.columns

temp.rename(columns={'index':'Variable'
                     ,0:'Q'}
            ,inplace=True)

# temp 

# Eliminar constantes
temp[(temp.Q == 1)]

Empty DataFrame
Columns: [Variable, Q]
Index: []

Missing

In [132]:
vars_with_na = [var for var in df.columns if df[var].isnull().sum() > 0]

# ordenamos por % de datos perdidos
temp = df[vars_with_na].isnull().mean().sort_values(ascending=False)
temp.shape


(0,)

Outliers

In [133]:
df.columns

Index(['Mean_Integrated', 'SD', 'EK', 'Skewness', 'Mean_DMSNR_Curve',
       'SD_DMSNR_Curve', 'EK_DMSNR_Curve', 'Skewness_DMSNR_Curve', 'Class'],
      dtype='object')

In [134]:
temp = df.copy()

vars = ['Mean_Integrated', 'SD', 'EK', 'Skewness', 'Mean_DMSNR_Curve',
    'SD_DMSNR_Curve', 'EK_DMSNR_Curve', 'Skewness_DMSNR_Curve']

for var in vars:
    # Variable original
    temp[var + '_ORI'] = temp[var]
    # Cuantil
    cuantil_1 = np.percentile(temp[var], 5)
    cuantil_95 = np.percentile(temp[var], 95)
    # Reemplazamos el valor mínimo y máximo
    temp.loc[temp[var] < cuantil_1,  var] = cuantil_1
    temp.loc[temp[var] > cuantil_95, var] = cuantil_95

In [135]:
temp[temp['Mean_DMSNR_Curve'] != temp['Mean_DMSNR_Curve_ORI']][['Mean_DMSNR_Curve', 'Mean_DMSNR_Curve_ORI']].head()

Mean_DMSNR_Curve  Mean_DMSNR_Curve_ORI
6             1.0059                0.9992
31            1.0059                0.6196
53            1.0059                0.7926
54            1.0059                0.8495
92           82.9670              146.5686

Discretisation

In [20]:
# Normalización

aux = temp[vars].copy()

scaler = MinMaxScaler(feature_range=(0, 1))
scaler = scaler.fit(aux)
aux = scaler.transform(aux)
normalized = pd.DataFrame(aux, columns=list(temp[vars].columns))
normalized.head(4)

Mean_Integrated     SD     EK  Skewness  Mean_DMSNR_Curve  SD_DMSNR_Curve  EK_DMSNR_Curve  Skewness_DMSNR_Curve
0           0.9707 0.9637 0.0000    0.0000            0.0268          0.1263          0.4885                0.2518
1           0.5260 1.0000 0.2372    0.0039            0.0082          0.0595          0.6592                0.4308
2           0.5319 0.2127 0.1889    0.1503            0.0258          0.1678          0.4728                0.2145
3           0.9261 1.0000 0.0556    0.0000            0.0322          0.1554          0.4177                0.1822

In [21]:
df[vars].shape, normalized.shape

((17898, 8), (17898, 8))

Clean Dataset

In [22]:
df_clean = pd.concat([df['Class'], normalized], axis=1)

In [97]:
df_clean.shape, df.shape

((17898, 9), (17898, 9))

# **[5] Feature Selection**

In [98]:
X = df_clean.drop('Class', axis=1)
y = df_clean['Class']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.30, random_state=42)

X_train.shape, X_test.shape

((12528, 8), (5370, 8))

In [99]:
# Eliminamos variables correlacionadas

n_max = 0.90

corr_features = correlation(X_train, n_max)
print('correlated features: ', len(set(corr_features)))

correlated features:  2


In [100]:
# Generamos nuevo dataset

X_train_selected = X_train.drop(labels=corr_features, axis=1) # , inplace=True
X_test_selected = X_test.drop(labels=corr_features, axis=1) # , inplace=True

X_train_selected.shape, X_test_selected.shape

((12528, 6), (5370, 6))

In [101]:
# Variables Finales
vars_final = X_train_selected.columns
vars_final

Index(['Mean_Integrated', 'SD', 'EK', 'Mean_DMSNR_Curve', 'SD_DMSNR_Curve',
       'EK_DMSNR_Curve'],
      dtype='object')

In [207]:
# Normalización con variables finales

aux = X_train_selected.copy()

scaler = MinMaxScaler(feature_range=(0, 1))
scaler = scaler.fit(aux)
aux = scaler.transform(aux)
normalized = pd.DataFrame(aux, columns=list(X_train_selected.columns))
normalized.head(4)

Mean_Integrated     SD     EK  Mean_DMSNR_Curve  SD_DMSNR_Curve  EK_DMSNR_Curve
0           0.7439 0.6277 0.2066            0.0264          0.1152          0.4540
1           0.2276 0.0672 0.3215            0.0170          0.1021          0.5829
2           0.8541 0.8509 0.1243            0.0212          0.1775          0.5235
3           1.0000 0.6504 0.0053            0.2009          0.6828          0.1593

# **[6] Train**

In [102]:
# Train Test Split

X = df_clean[vars_final]
y = df_clean['Class']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.30, random_state=42)

X_train.shape, X_test.shape

((12528, 6), (5370, 6))

In [103]:
# Train

indicadores_train = pd.DataFrame()
indicadores_test = pd.DataFrame()

temp_indicadores_train = pd.DataFrame()
temp_indicadores_test = pd.DataFrame()

#======= Parámetros

model_name = 'LogisticRegresion'

penalty = ['l1', 'l2', 'elasticnet'] # 'none'
C = np.logspace(-5, 5, 50)
solver = ['lbfgs', 'newton-cg', 'liblinear', 'sag', 'saga']
max_iter = [500]

params = {
    'penalty': penalty, 
    'C': C,
    'solver': solver,
    'max_iter': max_iter
    }

n_cores = round(psutil.cpu_count(logical = True)/2)

#======= Tiempo de Procesamiento del Modelo
tiempo_inicio_model = datetime.now()

#======= Entrenamiento GridSearchCV
temp_model = LogisticRegression(fit_intercept=True, random_state=42)

grid_search = GridSearchCV(estimator = temp_model,
    param_grid = params,
    scoring = "f1_weighted", 
    cv = 5, 
    n_jobs = n_cores, # -1
    verbose = 1) # 0 | True

grid_search.fit(X_train, y_train) 

#======= Mejor Modelo
temp_best_params = grid_search.best_params_
temp_best_score = grid_search.best_score_
# Hiperparámetros
temp_model = LogisticRegression(fit_intercept=True, random_state=42,
    penalty = temp_best_params['penalty'],
    C = temp_best_params['C'],
    solver = temp_best_params['solver'],
    max_iter = temp_best_params['max_iter']
    )
                    
temp_model.fit(X_train, y_train)

#======= Predictions
y_train_pred = temp_model.predict_proba(X_train)[:,1]
y_test_pred = temp_model.predict_proba(X_test)[:,1]

#======= Guardar Predictions
X_train[model_name + '_' + 'PREDICT'] = y_train_pred
X_test[model_name + '_' + 'PREDICT'] = y_test_pred

#======= Datos Modelo
temp_indicadores_train['BD'] = 'Train'
temp_indicadores_test['BD'] = 'Test'
# 
temp_indicadores_train['Modelo'] = [model_name]
temp_indicadores_test['Modelo'] = [model_name]
# 
temp_indicadores_train['NumeroVariables'] = len(vars_final)
temp_indicadores_test['NumeroVariables'] = len(vars_final)
#
temp_indicadores_train[list(temp_best_params)[0]] = temp_best_params['C']
temp_indicadores_train[list(temp_best_params)[1]] = temp_best_params['max_iter']
temp_indicadores_train[list(temp_best_params)[2]] = temp_best_params['penalty']
temp_indicadores_train[list(temp_best_params)[3]] = temp_best_params['solver']
#
temp_indicadores_test[list(temp_best_params)[0]] = temp_best_params['C']
temp_indicadores_test[list(temp_best_params)[1]] = temp_best_params['max_iter']
temp_indicadores_test[list(temp_best_params)[2]] = temp_best_params['penalty']
temp_indicadores_test[list(temp_best_params)[3]] = temp_best_params['solver']
#
temp_indicadores_train['BestScore'] = np.round(temp_best_score,4)*100
temp_indicadores_test['BestScore'] = np.round(temp_best_score,4)*100

#======= Indicadores Performance
# Categorías + Probabilidades
fpr, tpr, thresholds = roc_curve(y_train, y_train_pred)
temp_indicadores_train['AUC'] = np.round(auc(fpr, tpr),4)*100
fpr, tpr, thresholds = roc_curve(y_test, y_test_pred) # , pos_label=2
temp_indicadores_test['AUC'] = np.round(auc(fpr, tpr),4)*100
# 
temp_indicadores_train['Gini'] = np.round(temp_indicadores_train.AUC * 2 - 100,2)
temp_indicadores_test['Gini'] = np.round(temp_indicadores_test.AUC * 2 - 100,2)

#======= Indicadores Calibración
temp_indicadores_train['Brier'] = np.round(brier_score_loss(y_train, y_train_pred),4)*100
temp_indicadores_test['Brier'] = np.round(brier_score_loss(y_test, y_test_pred),4)*100

#======= Indicadores Clasificación
y_train_pred = temp_model.predict(X_train[vars_final])
y_test_pred = temp_model.predict(X_test[vars_final])
#
temp_indicadores_train['Accuracy'] = np.round(accuracy_score(y_train, y_train_pred),4)*100 
temp_indicadores_test['Accuracy'] = np.round(accuracy_score(y_test, y_test_pred),4)*100
#
temp_indicadores_train['Precision'] = np.round(precision_score(y_train, y_train_pred),4)*100 
temp_indicadores_test['Precision'] = np.round(precision_score(y_test, y_test_pred),4)*100 
#
temp_indicadores_train['Recall'] = np.round(recall_score(y_train, y_train_pred),4)*100 
temp_indicadores_test['Recall'] = np.round(recall_score(y_test, y_test_pred),4)*100 
#
temp_indicadores_train['F1_Score'] = np.round(f1_score(y_train, y_train_pred),4)*100
temp_indicadores_test['F1_Score'] = np.round(f1_score(y_test, y_test_pred),4)*100

#======= Tiempo de Procesamiento del Modelo
tiempo_fin_model = datetime.now()
tiempo_proc_model = tiempo_fin_model - tiempo_inicio_model
#
temp_indicadores_train['TiempoProc'] = round(tiempo_proc_model.total_seconds()/60,4)
temp_indicadores_test['TiempoProc'] = round(tiempo_proc_model.total_seconds()/60,4)

#======= Unificar
temp_indicadores_train['BD'] = 'Train'
temp_indicadores_test['BD'] = 'Test'
indicadores_train = pd.concat([indicadores_train, temp_indicadores_train], axis=0)
indicadores_test = pd.concat([indicadores_test, temp_indicadores_test], axis=0)

Fitting 5 folds for each of 750 candidates, totalling 3750 fits


In [104]:
# Indicadores
indicadores_lr = pd.concat([indicadores_train, indicadores_test], axis=0)
indicadores_lr

BD             Modelo  NumeroVariables       C  max_iter penalty     solver  BestScore     AUC    Gini  Brier  Accuracy  Precision  Recall  F1_Score  TiempoProc
0  Train  LogisticRegresion                6 86.8511       500      l1  liblinear    97.9200 97.8200 95.6400 1.7100   98.0000    94.7400 82.8300   88.3900      0.2969
0   Test  LogisticRegresion                6 86.8511       500      l1  liblinear    97.9200 97.4600 94.9200 1.7300   97.8800    94.0800 81.6900   87.4400      0.2969

In [112]:
# Arquitectura del mejor modelo

temp = indicadores_lr.copy()

temp_model_final = LogisticRegression(fit_intercept=True, random_state=42,
    penalty = indicadores_lr[indicadores_lr['BD'] == 'Train']['penalty'][0],
    C = indicadores_lr[indicadores_lr['BD'] == 'Train']['C'][0],
    solver = indicadores_lr[indicadores_lr['BD'] == 'Train']['solver'][0],
    max_iter = indicadores_lr[indicadores_lr['BD'] == 'Train']['max_iter'][0]
    )

temp_model_final.fit(X_train[vars_final], y_train)


LogisticRegression(C=86.85113737513521, max_iter=500, penalty='l1',
                   random_state=42, solver='liblinear')

# **[7] Exportar**

In [208]:
# Exportar Scaler
dump(scaler, 'scaler' + '.joblib')

['scaler.joblib']

In [114]:
# Exportar Modelo
dump(temp_model_final, 'model' + '.joblib')

['model.joblib']